In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/steam-sentiment-eng/sentiment_reviews_eng.csv
/kaggle/input/steam-reviews-2021/steam_reviews.csv


In [2]:
#!pip install vaderSentiment

In [3]:
#!pip install vaderSentiment

In [4]:
'''
import pandas as pd
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
import time
import csv

vader_analyzer = SentimentIntensityAnalyzer()

chunksize = 1000000

file_path = '/kaggle/input/steam-reviews-2021/steam_reviews.csv'

# sentiment analysis using VADER
def vader_sentiment_analysis(text):
    if pd.isna(text):
        return 'neutral'
    score = vader_analyzer.polarity_scores(text)['compound']
    if score >= 0.05:
        return 'positive'
    elif score <= -0.05:
        return 'negative'
    else:
        return 'neutral'

# Start the timer
start_time = time.time()

# Process the file in chunks
for i, chunk in enumerate(pd.read_csv(file_path, chunksize=chunksize, encoding='utf-8', 
                                      quoting=csv.QUOTE_MINIMAL, escapechar='\\', 
                                      on_bad_lines='skip', low_memory=False, dtype=str)):

    chunk = chunk[chunk['language'] == 'english'].copy()
    chunk['sentiment'] = chunk['review'].apply(lambda x: vader_sentiment_analysis(x))
    sentiment_chunk = chunk[['review_id', 'review', 'sentiment']]

    # Log 
    elapsed_time = time.time() - start_time
    print(f"\n--- Chunk {i + 1} processed ---")
    print(f"Time taken for this chunk: {elapsed_time:.2f} seconds")
    print(f"Sample of sentiment data:\n{sentiment_chunk.head()}\n")

    # Overwrite original file
    mode = 'w' if i == 0 else 'a' # w: "write" for the first chunk, a "append" for the next
    header = i == 0
    sentiment_chunk[['review_id', 'sentiment']].to_csv(sentiment_file_path, mode=mode, header=header, index=False)

# Calculate total time taken
total_time = time.time() - start_time
print(f"\n=== Total time taken for processing all chunks: {total_time:.2f} seconds ===")
'''

'\nimport pandas as pd\nfrom vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer\nimport time\nimport csv\n\nvader_analyzer = SentimentIntensityAnalyzer()\n\nchunksize = 1000000\n\nfile_path = \'/kaggle/input/steam-reviews-2021/steam_reviews.csv\'\n\n# sentiment analysis using VADER\ndef vader_sentiment_analysis(text):\n    if pd.isna(text):\n        return \'neutral\'\n    score = vader_analyzer.polarity_scores(text)[\'compound\']\n    if score >= 0.05:\n        return \'positive\'\n    elif score <= -0.05:\n        return \'negative\'\n    else:\n        return \'neutral\'\n\n# Start the timer\nstart_time = time.time()\n\n# Process the file in chunks\nfor i, chunk in enumerate(pd.read_csv(file_path, chunksize=chunksize, encoding=\'utf-8\', \n                                      quoting=csv.QUOTE_MINIMAL, escapechar=\'\\\', \n                                      on_bad_lines=\'skip\', low_memory=False, dtype=str)):\n\n    chunk = chunk[chunk[\'language\'] == \'english\']

In [5]:
'''
import pandas as pd

file_path = '/kaggle/input/steam-reviews-2021/steam_reviews.csv'
sentiment_file_path = '/kaggle/input/steam-sentiment-eng/sentiment_reviews_eng.csv'

# Process the file in chunks to avoid memory issues
chunksize = 1000000

# Initialize an empty list to collect chunks
merged_chunks = []

for chunk in pd.read_csv(file_path, chunksize=chunksize, encoding='utf-8', on_bad_lines='skip', low_memory=False, dtype=str):
    # Load the sentiment file
    sentiment_df = pd.read_csv(sentiment_file_path, dtype=str)
    
    # Merge each chunk with the sentiment DataFrame
    merged_chunk = chunk.merge(sentiment_df, on='review_id', how='left')
    
    # Append merged chunk to list
    merged_chunks.append(merged_chunk)

# Concatenate all merged chunks into a single DataFrame
merged_df = pd.concat(merged_chunks, ignore_index=True)
'''

"\nimport pandas as pd\n\nfile_path = '/kaggle/input/steam-reviews-2021/steam_reviews.csv'\nsentiment_file_path = '/kaggle/input/steam-sentiment-eng/sentiment_reviews_eng.csv'\n\n# Process the file in chunks to avoid memory issues\nchunksize = 1000000\n\n# Initialize an empty list to collect chunks\nmerged_chunks = []\n\nfor chunk in pd.read_csv(file_path, chunksize=chunksize, encoding='utf-8', on_bad_lines='skip', low_memory=False, dtype=str):\n    # Load the sentiment file\n    sentiment_df = pd.read_csv(sentiment_file_path, dtype=str)\n    \n    # Merge each chunk with the sentiment DataFrame\n    merged_chunk = chunk.merge(sentiment_df, on='review_id', how='left')\n    \n    # Append merged chunk to list\n    merged_chunks.append(merged_chunk)\n\n# Concatenate all merged chunks into a single DataFrame\nmerged_df = pd.concat(merged_chunks, ignore_index=True)\n"

In [6]:
#merged_df.head()

In [7]:
!pip install transformers

RuntimeError: The size of tensor a (894) must match the size of tensor b (512) at non-singleton dimension 1



In [8]:
import pandas as pd
from transformers import AutoTokenizer, AutoModelForSequenceClassification, pipeline
from datasets import Dataset
import torch
import time
import csv
import re

# Check if GPU is available and set the device
device = 0 if torch.cuda.is_available() else -1

# Manually load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("uer/roberta-base-finetuned-jd-binary-chinese")
model = AutoModelForSequenceClassification.from_pretrained("uer/roberta-base-finetuned-jd-binary-chinese")

# Initialize pipeline with the manually loaded model and tokenizer, and set truncation
sentiment_pipeline = pipeline("sentiment-analysis", model=model, tokenizer=tokenizer, device=device,
                              max_length=512, truncation=True)

# Define file paths
file_path = '/kaggle/input/steam-reviews-2021/steam_reviews.csv'
sentiment_file_path = 'sentiment_values_schinese.csv'

def analyze_text(batch):
    results = sentiment_pipeline(batch["review"])
    
    # Initialize lists to store final sentiment and score
    sentiments = []
    scores = []
    
    # Determine final sentiment and store score
    for text, res in zip(batch["review"], results):
        # Remove any text in parentheses from the label (if applicable)
        clean_label = re.sub(r"\s*\(.*?\)", "", res['label'])

        # Determine final sentiment based on score and label
        if res['score'] > 0.6:
            final_sentiment = "positive" if clean_label == "positive" else "negative"
        elif 0.4 <= res['score'] <= 0.6:
            final_sentiment = "neutral"
        else:
            final_sentiment = "negative"  # for scores below 0.4, assume negative by default
        
        # Append sentiment and score
        sentiments.append(final_sentiment)
        scores.append(res['score'])
        
        # Print detailed output for debugging
        #print(f"Text: {text[:100]}...")  # Display up to the first 100 characters of the text
        #print(f"Model Prediction: {clean_label}")
        #print(f"Score: {res['score']:.4f}")
        #print(f"Final Sentiment: {final_sentiment}")
        #print("-" * 50)

    # Directly assign computed sentiments and scores to the batch DataFrame
    batch["sentiment"] = sentiments
    batch["score"] = scores
    
    return batch


def process_chunks(file_path, chunksize):
    start_time = time.time()
    chunk_count = 0
    
    # Initialize output file with headers
    with open(sentiment_file_path, 'w', newline='', encoding='utf-8') as f:
        writer = csv.writer(f)
        writer.writerow(['review_id', 'review', 'sentiment', 'score'])

    # Read and process data in chunks
    for chunk in pd.read_csv(file_path, chunksize=chunksize, encoding='utf-8', 
                             quoting=csv.QUOTE_MINIMAL, escapechar='\\', 
                             on_bad_lines='skip', low_memory=False, dtype=str):
        
        chunk_count += 1
        print(f"\nProcessing chunk {chunk_count}...")

        # Filter for Simplified Chinese (schinese) language reviews
        schinese_reviews = chunk[chunk['language'] == 'schinese'].copy()
        chinese_count = len(schinese_reviews)
        
        if chinese_count > 0:
            # Ensure all reviews are valid strings
            schinese_reviews['review'] = schinese_reviews['review'].fillna("").astype(str)
            
            # Create a Hugging Face Dataset from the DataFrame
            dataset = Dataset.from_pandas(schinese_reviews[['review_id', 'review']])

            # Process each batch and add sentiment analysis results
            sentiment_dataset = dataset.map(analyze_text, batched=True, batch_size=64)
            sentiment_df = sentiment_dataset.to_pandas()

            # Debug: Show a sample of the processed chunk including score
            print(f"Sample processed data for chunk {chunk_count}:\n{sentiment_df[['review_id', 'review', 'sentiment', 'score']].head()}")
            print(f"Number of Chinese reviews in chunk {chunk_count}: {chinese_count}")

            # Append processed data to CSV including score
            sentiment_df[['review_id', 'review', 'sentiment']].to_csv(
                sentiment_file_path, mode='a', header=False, index=False
            )

    total_time = time.time() - start_time
    print(f"\n=== Total processing time: {total_time:.2f} seconds ===")

# Process the dataset with optimized chunk size
process_chunks(file_path, chunksize=50000)  # Maximum chunk size by Pc could handle


tokenizer_config.json:   0%|          | 0.00/295 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/612 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/110k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/409M [00:00<?, ?B/s]

...

Sample processed data for chunk 433:
  review_id                                             review sentiment  \
0  31296049  手残末日，我连打小姐姐都死得不要不要的。\n音乐画风都不错。\n英文文本太文艺的，一句话蹦五...  positive   
1  31294521  画面非常漂亮精致，但是bgm稍微弱了点，在游戏中感觉bgm可有可无，希望官方能给出汉化版本\...  positive   
2  31294236  诚意满满的一款艺术品，难以置信的游戏体验，无论是画面还是音乐、关卡还是剧情，都塑造精致、令人...  positive   
3  31276885                                          最新版本还是会掉帧  positive   
4  31274682  21h后的感慨：第一周目通关，完成度只有70%，仿佛又看到了第一次晓夜圆舞曲通关时因为不知道...  positive   

      score  
0  0.991407  
1  0.982932  
2  0.990058  
3  0.893303  
4  0.870134  
Number of Chinese reviews in chunk 433: 9873

Processing chunk 434...


Map:   0%|          | 0/6930 [00:00<?, ? examples/s]

Sample processed data for chunk 434:
  review_id                                             review sentiment  \
0  41885610  本来以为过了英语六级玩这个全英版的游戏会没什么问题的。然鹅在游戏中还是遇到了很多语言上的麻烦...  positive   
1  39761323  通关之后，怎么说呢，没有什么特别的感觉。\n画面：作为像素游戏，我感觉可以把本游戏划分到好的...  negative   
2  36314518                                               索然无味  negative   
3  34409424                           zhe ge you xi hen niu bi  negative   
4  31551277  [h1][b]《银莲花公园》[/b]卢卡斯艺术的梦想变成了Ron的玩具[/h1]\n\n太长...  positive   

      score  
0  0.989864  
1  0.945499  
2  0.940480  
3  0.669240  
4  0.944286  
Number of Chinese reviews in chunk 434: 6930

Processing chunk 435...


Map:   0%|          | 0/2235 [00:00<?, ? examples/s]

Sample processed data for chunk 435:
  review_id                                             review sentiment  \
0  80673204  第一次评论送给Alyx了。库里真爱的游戏不少，但是一直很懒都不会去写评论。直到玩到了Alyx...  positive   
1  80670258                 太棒了，近几年玩到的最棒的一款游戏了，体验这种身临其境的感觉就是享受  positive   
2  80661685                                              GREAT  positive   
3  80655814                  我心目中的2019-20年度最佳，美末2给爷爪巴\n半条命yyds  positive   
4  80652443              VR游戏的灯塔\n打之前要谨慎考虑\n戒游戏的神器，打了就不想打屏显游戏了   neutral   

      score  
0  0.896674  
1  0.993767  
2  0.970886  
3  0.896895  
4  0.567973  
Number of Chinese reviews in chunk 435: 2235

=== Total processing time: 36231.80 seconds ===


In [9]:
import pandas as pd
df = pd.read_csv('/kaggle/working/sentiment_values_schinese.csv')


/tmp/ipykernel_23/1226659294.py:2: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('/kaggle/working/sentiment_values_schinese.csv')


In [10]:
#!pip install deeppavlov

In [11]:
'''
import time
import csv
from deeppavlov import build_model

# Load the DeepPavlov Russian sentiment analysis model
model = build_model('rusentiment_bert', download=True, install=True)
'''

"\nimport time\nimport csv\nfrom deeppavlov import build_model\n\n# Load the DeepPavlov Russian sentiment analysis model\nmodel = build_model('rusentiment_bert', download=True, install=True)\n"

In [12]:
'''
# Define a function for sentiment analysis using DeepPavlov
def deeppavlov_sentiment_analysis(text):
    if pd.isna(text):
        print("Review is NaN, assigning 'neutral'.")
        return 'neutral'
    
    # Use the DeepPavlov model to predict the sentiment
    result = model([text])[0]  # The model returns a list, so we take the first element
    print(f"Processing review: {text}")
    print(f"Assigned sentiment: {result}")
    
    return result

# Process the file in chunks and save the sentiment values separately
def process_and_log_workflow(file_path, chunksize):
    # Start the timer
    start_time = time.time()

    # Read the dataset in chunks
    for i, chunk in enumerate(pd.read_csv(file_path, chunksize=chunksize, encoding='utf-8', 
                                          quoting=csv.QUOTE_MINIMAL, escapechar='\\', 
                                          on_bad_lines='skip', low_memory=False, dtype=str)):
        
        # Filter for Russian ('russian') reviews only and explicitly create a copy
        chunk = chunk[chunk['language'] == 'russian'].copy()
        
        # Check if the chunk has any Russian reviews
        if not chunk.empty:
            # Apply the sentiment analysis with detailed logging for each row
            chunk['sentiment'] = chunk['review'].apply(deeppavlov_sentiment_analysis)
            sentiment_chunk = chunk[['review_id', 'review', 'sentiment']]
            
            # Log a sample of the processed chunk for clarity
            print(f"\n--- Chunk {i + 1} processed ---")
            print(f"Time taken for this chunk: {time.time() - start_time:.2f} seconds")
            print(f"Sample of sentiment data:\n{sentiment_chunk.head()}\n")
        else:
            print(f"\n--- Chunk {i + 1} contains no Russian reviews ---")

    total_time = time.time() - start_time
    print(f"\n=== Total time taken for processing all chunks: {total_time:.2f} seconds ===")

# Run the processing function with detailed logging
process_and_log_workflow(file_path, chunksize=1000)  # Adjust chunksize based on memory capacity
'''

'\n# Define a function for sentiment analysis using DeepPavlov\ndef deeppavlov_sentiment_analysis(text):\n    if pd.isna(text):\n        print("Review is NaN, assigning \'neutral\'.")\n        return \'neutral\'\n    \n    # Use the DeepPavlov model to predict the sentiment\n    result = model([text])[0]  # The model returns a list, so we take the first element\n    print(f"Processing review: {text}")\n    print(f"Assigned sentiment: {result}")\n    \n    return result\n\n# Process the file in chunks and save the sentiment values separately\ndef process_and_log_workflow(file_path, chunksize):\n    # Start the timer\n    start_time = time.time()\n\n    # Read the dataset in chunks\n    for i, chunk in enumerate(pd.read_csv(file_path, chunksize=chunksize, encoding=\'utf-8\', \n                                          quoting=csv.QUOTE_MINIMAL, escapechar=\'\\\', \n                                          on_bad_lines=\'skip\', low_memory=False, dtype=str)):\n        \n        # Filter 